In [1]:
import os, random, sumolib
import sumolib
import pandas as pd
import numpy as np
from datetime import datetime

In [2]:
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_dayplan = os.path.join(path_root, 'data', 'tables', '20240729', 'TC_IF_TOD_DAY_PLAN.csv')
path_sigl_cycl = os.path.join(path_root, 'test_0729', 'data', 'tables', 'TL_IF_SIGL_CYCL.csv')
dayplan = pd.read_csv(path_dayplan)
CRSRD_IDs = [436, 437, 438, 442, 443, 455, 456, 457, 458]
dayplan = dayplan[dayplan.CRSRD_ID.isin(CRSRD_IDs)]

dayplan = dayplan.drop(columns=['LAST_MDFCN_DT'])

In [3]:
midnight = int(datetime(2024, 7, 29).timestamp())
next_day = int(datetime(2024, 7, 30).timestamp())

histories = []

for CRSRD_ID in CRSRD_IDs:
    dplan = dayplan[dayplan.CRSRD_ID==CRSRD_ID]
    if ((dplan.HOUR==0) & (dplan.MIN==0)).any():
        pass
    else:
        dplan_temp = dplan[-1:]
        dplan_temp['HOUR'] = 0
        dplan_temp['MIN'] = 0
        dplan = pd.concat([dplan, dplan_temp])
    dplan = dplan.sort_values(by=['HOUR', 'MIN']).reset_index(drop=True)
    dplan.loc[:, 'end_unix'] = dplan['HOUR'].astype(int) * 3600 + dplan['MIN'].astype(int) * 60 + midnight
    history = []
    current_time = midnight
    for i in range(len(dplan)):
        row = dplan.iloc[i]
        cycle = row.CYCL
        offset = row.OFFSET
        unix_end = dplan.iloc[i+1]['end_unix'] if i < len(dplan) - 1 else next_day
        r = 0
        while current_time <= unix_end:
            remainder = current_time % 10
            if remainder != 0:  # 현재시각의 일의자리가 0이 아니면 다음 현재시각의 일의자리가 0이 되도록 맞춰준다.
                r = (5 - remainder) % 10 - 5 # 1>-1, 2>-2, 3>-3, 4>-4, 5>-5, 6>4, 7>3, 8>2, 9>1
            else:
                r = random.choices([0, -1, 1], weights=[10, 1, 1])[0] # 측정오차
            # 0.001의 확률로 결측 발생
            if random.random() < 0.001: # 주기의 배수만큼 결측
                n = random.randint(0,100)
                current_time += n * cycle + r
            # 0.01의 확률로 이상치 발생
            elif random.random() > 0.99: # 카이제곱분포값 * 주기만큼의 이상치 발생. 카이제곱분포값은 항상 양수이고 평균이 1
                current_time += int(np.random.chisquare(df=1) * cycle) + r
            else:
                current_time += cycle + r # 결측/이상 없음
            new_row = row.copy()
            new_row['PHASE_DT'] = current_time
            new_row['CYCL'] = cycle
            new_row['OFFSET'] = offset
            history.append(new_row)
    history = pd.concat(history, axis=1).transpose()
    history = history[['PHASE_DT', 'CRSRD_ID']
                    + [f'RING{alph}_PHASE{i}' for alph in ['A', 'B'] for i in range(1,9)]]
    history = history[history.PHASE_DT <= next_day]
    history = history.rename(columns={'PHASE_DT':'OCRN_DT'})
    histories.append(history)
histories = pd.concat(histories)

In [4]:
histories = histories.sort_values(by=['OCRN_DT', 'CRSRD_ID'])
histories = histories.reset_index(drop=True)
histories['FRST_REG_DT'] = ''
histories['OCRN_DT'] = pd.to_datetime(histories['OCRN_DT'], unit='s')
histories['OCRN_DT'] = histories['OCRN_DT'].dt.strftime('%Y-%m-%d %H:%M:%S.%f').str[:-3]
histories.to_csv(path_sigl_cycl, index=False)

In [5]:
print(path_sigl_cycl)

c:\github\siggen\test_0729\data\tables\TL_IF_SIGL_CYCL.csv
